### In this demo, you'll see different modes of AES block cipher and their properties.

In [1]:
from Crypto.Cipher import AES # NOTE: you may need to install PyCrypto package
from Crypto.Random import get_random_bytes
from Crypto.Util import Counter
import random

In [2]:
def pad(data, length=16):
    """pads data to nearest multiple of length (default 16 bytes = 128 bits)"""
    return data + "-" * (16 - (len(data) % length))

def hexify(data):
    # Source: https://stackoverflow.com/questions/12214801/print-a-string-as-hex-bytes
    return ":".join("{:02x}".format(c) for c in data)
    

plaintext = "The world wonders"
            #----------------=
    
# Some modes of operation require padding to nearest 128 bits (16 bytes)
plaintext_padded = pad(plaintext)

key = get_random_bytes(16)

In [3]:
def blockPrint(data):
    index = 0
    hexdata = ":".join("{:02x}".format(c) for c in data)
    length = len(hexdata)
    while index < length:
        print(hexdata[index:min(index + 2*16 + 15, length)])
        index += 3*16

def xorBlockPrint(c1, c2):
    index = 0
    xor = ":".join(["{:02x}".format(c1[c] ^ c2[c]) for c in range(len(c1))]).replace("00", "--")
    length = len(xor)
    while index < length:
        print(xor[index:min(index + 2*16 + 15, length)])
        index += 3*16

In [4]:
def encryptRandom(algorithm, plaintext1, plaintext2):
    """Encrypts either plaintext at random and returns the ciphertext.
       Used when playing IND-CPA games."""
    to_encrypt = 1 if random.random() > 0.5 else 0
    print(f"Oracle encrypts plaintext {to_encrypt+1}\n")
    return algorithm.encrypt((plaintext1, plaintext2)[to_encrypt])

## IND-CPA with deterministic algorithm: AES-ECB

### Encryption

In [5]:
AES_ECB = AES.new(key, AES.MODE_ECB)

print("Encryption of: ", plaintext_padded)
blockPrint(AES_ECB.encrypt(plaintext_padded))

Encryption of:  The world wonders---------------
71:a5:7c:1f:00:e2:d7:da:a7:fb:e8:cc:36:a8:1e:db
fc:50:fb:99:7e:fe:8c:3e:ba:30:43:d3:df:b1:ee:91


#### If you reencrypt the same plaintext, the ciphertext is identical.

In [6]:
print("Encryption of: ", plaintext_padded)
blockPrint(AES_ECB.encrypt(plaintext_padded))

Encryption of:  The world wonders---------------
71:a5:7c:1f:00:e2:d7:da:a7:fb:e8:cc:36:a8:1e:db
fc:50:fb:99:7e:fe:8c:3e:ba:30:43:d3:df:b1:ee:91


### Decryption

In [7]:
ciphertext = AES_ECB.encrypt(plaintext_padded)
print("Decryption of: ")
blockPrint(ciphertext)
print(AES_ECB.decrypt(ciphertext))

Decryption of: 
71:a5:7c:1f:00:e2:d7:da:a7:fb:e8:cc:36:a8:1e:db
fc:50:fb:99:7e:fe:8c:3e:ba:30:43:d3:df:b1:ee:91
b'The world wonders---------------'


### For an attacker, winning the IND-CPA game against AES-ECB is easy.

In [8]:
"""Wins the IND-CPA game against AES-ECB as an attacker."""

# Main game: provide two plaintexts, cipher selects one
plaintext1 = pad("This is a plaintext")
plaintext2 = pad("A completely different one")
ciphertext = encryptRandom(AES_ECB, plaintext1, plaintext2)
print("Ciphertext returned by the oracle:")
blockPrint(ciphertext)

# Attacker can obtain additional encryptions of plaintexts.
ciphertext1 = AES_ECB.encrypt(plaintext1)
ciphertext2 = AES_ECB.encrypt(plaintext2)
print("\nEncryption of plaintext 1:")
blockPrint(ciphertext1)
print("\nEncryption of plaintext 2:")
blockPrint(ciphertext2)

# Make a guess!
if ciphertext == ciphertext1:
    print("\nOracle's ciphertext is encryption of plaintext 1")
else:
    print("\nOracle's ciphertext is encryption of plaintext 2")

Oracle encrypts plaintext 2

Ciphertext returned by the oracle:
72:49:b8:03:2b:6e:bb:b1:ac:9c:0d:d7:96:0b:09:d4
01:ea:95:ee:46:a6:1a:8e:d9:5a:b2:37:91:f4:6a:0a

Encryption of plaintext 1:
c4:b8:68:2b:36:b7:a8:41:d2:8d:53:82:87:16:97:e8
a9:98:95:5c:b0:e3:15:c7:9a:cf:60:c6:eb:71:d6:90

Encryption of plaintext 2:
72:49:b8:03:2b:6e:bb:b1:ac:9c:0d:d7:96:0b:09:d4
01:ea:95:ee:46:a6:1a:8e:d9:5a:b2:37:91:f4:6a:0a

Oracle's ciphertext is encryption of plaintext 2


## IND-CPA with nondeterministic algorithm: AES-CTR

### Encryption

In [9]:
print("Encryption of: ", plaintext) #Notice no padding is required!
IV = get_random_bytes(8)
print("IV used: ", hexify(IV))
blockPrint(AES.new(key, AES.MODE_CTR, counter=Counter.new(64, prefix=IV)).encrypt(plaintext))

Encryption of:  The world wonders
IV used:  9f:d8:a6:48:d3:c7:1e:a3
96:2b:66:d2:13:6b:fa:4d:9e:79:73:69:f8:72:28:08
ef


#### If you reencrypt the same plaintext with a different IV, the ciphertext is different. This makes an encryption scheme IND-CPA since no correlation can be established between multiple encryptions of similar or same plaintext.

In [10]:
print("Encryption of: ", plaintext)
IV = get_random_bytes(8)
print("IV used: ", hexify(IV))
blockPrint(AES.new(key, AES.MODE_CTR, counter=Counter.new(64, prefix=IV)).encrypt(plaintext))

Encryption of:  The world wonders
IV used:  af:fe:4d:5a:aa:03:94:c0
f7:de:91:9b:c7:ca:65:60:ba:f2:c0:5b:06:3f:b6:36
9c


#### However, if you reencrypt the same plaintext with the same IV, the ciphertext is identical.

In [11]:
print("Two encryptions of: ", plaintext)
IV = get_random_bytes(8)
print("IV used: ", hexify(IV))
print("First encryption:")
blockPrint(AES.new(key, AES.MODE_CTR, counter=Counter.new(64, prefix=IV)).encrypt(plaintext))
print("\nSecond encryption:")
blockPrint(AES.new(key, AES.MODE_CTR, counter=Counter.new(64, prefix=IV)).encrypt(plaintext))

Two encryptions of:  The world wonders
IV used:  b7:37:26:41:39:9d:64:47
First encryption:
54:e8:b9:58:61:a5:24:51:49:26:4c:e5:1e:93:b5:c6
a3

Second encryption:
54:e8:b9:58:61:a5:24:51:49:26:4c:e5:1e:93:b5:c6
a3


### Again, wining the IND-CPA game against AES-CTR with IV reuse is easy.

In [12]:
"""Wins the IND-CPA game against AES-CTR with IV reuse as an attacker."""

#Generate IV to reuse
IV = get_random_bytes(8) 

# Main game: provide two plaintexts, cipher selects one
plaintext1 = "A good plaintext to encrypt"
plaintext2 = "This is another one for you"
ciphertext = encryptRandom(AES.new(key, AES.MODE_CTR, counter=Counter.new(64, prefix=IV)), plaintext1, plaintext2)
print("Ciphertext returned by the oracle:")
blockPrint(ciphertext)

# Attacker can obtain additional encryptions of plaintexts.
ciphertext1 = AES.new(key, AES.MODE_CTR, counter=Counter.new(64, prefix=IV)).encrypt(plaintext1)
ciphertext2 = AES.new(key, AES.MODE_CTR, counter=Counter.new(64, prefix=IV)).encrypt(plaintext2)
print("\nEncryption of plaintext 1:")
blockPrint(ciphertext1)
print("\nEncryption of plaintext 2:")
blockPrint(ciphertext2)

#Make a guess!
if ciphertext == ciphertext1:
    print("\nOracle's ciphertext is encryption of plaintext 1")
else:
    print("\nOracle's ciphertext is encryption of plaintext 2")

Oracle encrypts plaintext 1

Ciphertext returned by the oracle:
db:8c:38:3c:54:11:1e:4d:2b:88:f2:c3:ce:30:5f:fa
a9:96:dc:65:bd:67:59:da:a9:12:fc

Encryption of plaintext 1:
db:8c:38:3c:54:11:1e:4d:2b:88:f2:c3:ce:30:5f:fa
a9:96:dc:65:bd:67:59:da:a9:12:fc

Encryption of plaintext 2:
ce:c4:36:20:1b:1c:4d:1d:26:87:f4:d9:d2:30:55:ae
e6:8c:d6:65:be:66:48:88:a9:0d:fd

Oracle's ciphertext is encryption of plaintext 1


# IV compromise
If you encrypt a same plaintext with the same IV, two ciphertexts will be identical regardless of the mode of operation. If you encrypt two different plaintexts with the same IV, though, different modes of operation have differing levels of failure. In this section, you will analyze what happens when IV is reused in various AES modes of operation.

## IV reuse in synchronous stream ciphers [AES-CTR and AES-OFB]
Synchronous stream ciphers generate a psuedorandom bit stream that is combined (usually using xor) with plaintext, emulating One Time Pad (OTP). A Synchronous stream cipher's psuedorandom bit stream is dependent only on the key and IV: Plaintext does not affect the bitstream.

Since the bitstream is only dependent on the key and IV, IV reuse creates an OTP reuse scenario acoss the entire ciphertext. 

In [13]:
# Generate IV to reuse
IV = get_random_bytes(16)

# Note one byte of the plaintexts differ in the second block.
plaintext1 = "The plaintext is designed to occupy three blocks"
             #----------------================---------------- Exactly three blocks
plaintext2 = "The plaintext is designed To occupy three blocks"

# OFB mode of operation
ciphertext1 = AES.new(key, AES.MODE_OFB, IV=IV).encrypt(plaintext1)
ciphertext2 = AES.new(key, AES.MODE_OFB, IV=IV).encrypt(plaintext2)
print("\nEncryption of plaintext 1:")
blockPrint(ciphertext1)
print("\nEncryption of plaintext 2:")
blockPrint(ciphertext2)

print("\nxor of two plaintexts:")
xorBlockPrint([ord(c) for c in plaintext1], [ord(c) for c in plaintext2])

print("\nxor of two ciphertexts:")
xorBlockPrint(ciphertext1, ciphertext2)


Encryption of plaintext 1:
6b:2d:6e:29:b3:ca:16:9e:db:72:0f:41:94:b4:fc:ef
89:c3:e8:7e:e8:5c:94:01:be:d1:b3:c9:68:fb:cb:34
3a:a3:d3:14:ed:9c:eb:e7:3c:98:e6:eb:4c:f5:29:84

Encryption of plaintext 2:
6b:2d:6e:29:b3:ca:16:9e:db:72:0f:41:94:b4:fc:ef
89:c3:e8:7e:e8:5c:94:01:be:d1:93:c9:68:fb:cb:34
3a:a3:d3:14:ed:9c:eb:e7:3c:98:e6:eb:4c:f5:29:84

xor of two plaintexts:
--:--:--:--:--:--:--:--:--:--:--:--:--:--:--:--
--:--:--:--:--:--:--:--:--:--:20:--:--:--:--:--
--:--:--:--:--:--:--:--:--:--:--:--:--:--:--:--

xor of two ciphertexts:
--:--:--:--:--:--:--:--:--:--:--:--:--:--:--:--
--:--:--:--:--:--:--:--:--:--:20:--:--:--:--:--
--:--:--:--:--:--:--:--:--:--:--:--:--:--:--:--


You can tell the two plaintexts are identical except for one byte by only looking at the ciphertexts.

## IV reuse in AES-CFB
AES-CFB uses cipher feedback, which incorporates previous block of plaintext to the input of next block cipher. In case of IV reuse, all ciphertext blocks up to and including the block containing the first differing bit is subject to OTP reuse scenario.

In [14]:
# Generate IV to reuse
IV = get_random_bytes(16)

# Note one byte of the plaintexts differ in the second block.
plaintext1 = "the plaintext is designed to occupy three blocks"
             #----------------================---------------- Exactly three blocks
plaintext2 = "the plaintext is designed To occupy three blocks"

# CFB mode of operation
ciphertext1 = AES.new(key, AES.MODE_CFB, IV=IV, segment_size=128).encrypt(plaintext1)
ciphertext2 = AES.new(key, AES.MODE_CFB, IV=IV, segment_size=128).encrypt(plaintext2)
print("\nEncryption of plaintext 1:")
blockPrint(ciphertext1)
print("\nEncryption of plaintext 2:")
blockPrint(ciphertext2)

print("\nxor of two plaintexts:")
xorBlockPrint([ord(c) for c in plaintext1], [ord(c) for c in plaintext2])

print("\nxor of two ciphertexts:")
xorBlockPrint(ciphertext1, ciphertext2)


Encryption of plaintext 1:
7c:59:06:5b:9c:2b:4c:9a:65:cf:fb:03:1c:ad:1c:83
37:26:1a:c7:24:91:53:c6:62:ea:1c:4b:6f:a5:70:5e
14:9e:43:09:c4:cd:72:2e:c1:f4:f9:5e:ee:7c:25:f2

Encryption of plaintext 2:
7c:59:06:5b:9c:2b:4c:9a:65:cf:fb:03:1c:ad:1c:83
37:26:1a:c7:24:91:53:c6:62:ea:3c:4b:6f:a5:70:5e
ba:bf:c2:6b:8b:19:f7:0f:48:b0:89:e5:bf:de:f3:65

xor of two plaintexts:
--:--:--:--:--:--:--:--:--:--:--:--:--:--:--:--
--:--:--:--:--:--:--:--:--:--:20:--:--:--:--:--
--:--:--:--:--:--:--:--:--:--:--:--:--:--:--:--

xor of two ciphertexts:
--:--:--:--:--:--:--:--:--:--:--:--:--:--:--:--
--:--:--:--:--:--:--:--:--:--:20:--:--:--:--:--
ae:21:81:62:4f:d4:85:21:89:44:70:bb:51:a2:d6:97


## IV reuse in AES-CBC
AES-CBC inporporates plaintext block to the input of the block cipher. In case of IV reuse, all ciphertext blocks up to but not including the block containing the first differing bit is subject to OTP reuse scenario.

In [15]:
# Generate IV to reuse
IV = get_random_bytes(16)

# Note one byte of the plaintexts differ in the second block.
plaintext1 = "The plaintext is designed to occupy three blocks"
             #----------------================---------------- Exactly three blocks
plaintext2 = "The plaintext is designed To occupy three blocks"

# CBC mode of operation
ciphertext1 = AES.new(key, AES.MODE_CBC, IV=IV).encrypt(plaintext1)
ciphertext2 = AES.new(key, AES.MODE_CBC, IV=IV).encrypt(plaintext2)
print("\nEncryption of plaintext 1:")
blockPrint(ciphertext1)
print("\nEncryption of plaintext 2:")
blockPrint(ciphertext2)

print("\nxor of two plaintexts:")
xorBlockPrint([ord(c) for c in plaintext1], [ord(c) for c in plaintext2])

print("\nXor of two ciphertexts:")
xorBlockPrint(ciphertext1, ciphertext2)


Encryption of plaintext 1:
5d:1b:83:86:c7:d6:72:75:cf:c5:b7:5c:df:63:be:d2
a5:eb:da:e1:57:32:d1:18:3e:ad:f0:5a:5d:6b:c2:cf
64:c3:fa:ea:18:2a:40:7c:8d:59:35:2a:33:b3:15:35

Encryption of plaintext 2:
5d:1b:83:86:c7:d6:72:75:cf:c5:b7:5c:df:63:be:d2
d9:49:58:bb:c2:e8:55:8e:18:09:de:72:93:ec:bf:62
82:6a:6f:65:b2:67:d1:24:8f:22:62:a3:97:a8:bd:3c

xor of two plaintexts:
--:--:--:--:--:--:--:--:--:--:--:--:--:--:--:--
--:--:--:--:--:--:--:--:--:--:20:--:--:--:--:--
--:--:--:--:--:--:--:--:--:--:--:--:--:--:--:--

Xor of two ciphertexts:
--:--:--:--:--:--:--:--:--:--:--:--:--:--:--:--
7c:a2:82:5a:95:da:84:96:26:a4:2e:28:ce:87:7d:ad
e6:a9:95:8f:aa:4d:91:58:02:7b:57:89:a4:1b:a8:09


## Predictable IV in AES-CBC causes it to be IND-CPA insecure.
AES-CBC inporporates plaintext block to the input of the block cipher. This means if the IV is known in advance, the attacker can choose a plaintext that forces a specific input into the block cipher.

In [16]:
"""Wins the IND-CPA game against AES-CBC with predictable IV as an attacker."""

# Generate three IVs known in advance
IV1 = get_random_bytes(16)
IV2 = get_random_bytes(16)

# Note one byte of the plaintexts differ in the second block.
# Encode with utf-8 as we will be doing some xor black magic
plaintext1 = "Plain Plaintext.".encode('utf-8')
             #---------------- Exactly one block
plaintext2 = "Spicy Plaintext.".encode('utf-8')

ciphertext = encryptRandom(AES.new(key, AES.MODE_CBC, IV=IV1), plaintext1, plaintext2)
print("Ciphertext returned by the oracle:")
blockPrint(ciphertext)

forged = bytes([plaintext1[i] ^ IV1[i] ^ IV2[i] for i in range(len(plaintext1))])
# Attacker can obtain additional encryptions of plaintexts.
ciphertext1 = AES.new(key, AES.MODE_CBC, IV=IV2).encrypt(forged)

print("\nEncryption of forged ciphertext:")
blockPrint(ciphertext1)

# Make a guess!
if ciphertext == ciphertext1:
    print("\nOracle's ciphertext is encryption of plaintext 1")
else:
    print("\nOracle's ciphertext is encryption of plaintext 2")

Oracle encrypts plaintext 2

Ciphertext returned by the oracle:
57:f4:9a:1b:43:a1:3e:bc:71:df:a8:cd:49:70:71:47

Encryption of forged ciphertext:
78:83:35:c8:e6:35:2d:01:89:53:65:64:b7:9f:ff:d9

Oracle's ciphertext is encryption of plaintext 2


## Conclusion: 
Nondeterministic algorithms rely on IV to provide randomness. Reusing IV or letting attacker predict IV may compromise cipher integrity in various levels depending on the mode of operation.